In [2]:
# check installation of python 
! which python

# check installation of pip
! which pip

# upgrade pip if needed 
! pip install --upgrade pip

# install biopython
! pip install biopython

# upgrade biopython if needed 

! pip install biopython --upgrade

# import biopython and check import
import Bio
print(Bio.__version__)

/Users/giana.cirolia/anaconda3/bin/python
/Users/giana.cirolia/anaconda3/bin/pip
     |████████████████████████████████| 1.5 MB 2.6 MB/s eta 0:00:01
  Attempting uninstall: pip
    Found existing installation: pip 21.0
    Uninstalling pip-21.0:
      Successfully uninstalled pip-21.0
1.78


In [3]:
from Bio.Blast import NCBIXML
from collections import defaultdict
from Bio import SeqIO

In [203]:
## import command line interface for biopython blasts 
## more documentation here https://biopython.org/docs/1.75/api/Bio.Blast.Applications.html
from Bio.Blast.Applications import NcbiblastnCommandline

In [200]:
## make a blast search with gene and jakes minimal enhacer to the database to select only contigs with both the gene and the enhancer 
! mkdir -p database/output
cline = NcbiblastnCommandline(query="../sequences/queries/at.fasta" , db="../database/tes_db", strand="both", out="../database/output/test.xml", outfmt=5, task= "dc-megablast")
cline
print(cline)
cline()

blastn -out ../database/output/test.xml -outfmt 5 -query ../sequences/queries/at.fasta -db ../database/tes_db -strand both -task dc-megablast


('', '')

In [201]:
## Quick visual evaluation
E_VALUE_THRESH = 1000
MATCH_LENGTH = 0
for record in NCBIXML.parse(open("../database/output/test.xml", 'r')):
     if record.alignments:
            query = record.query[0:100].upper()
            print("\n")
            print("query", query)
            print("\n")
            for alignment in record.alignments:
                for hsp in alignment.hsps:
                    contig_length= alignment.length
                    contig_name = alignment.title
                    query_match_start = hsp.query_start
                    query_match_end = hsp.query_end
                    contig_match_start = hsp.sbjct_start
                    contig_match_end = hsp.sbjct_end
                    total_match = query_match_end - query_match_start
                    e_value = hsp.expect
                    BLAST_score = hsp.score
                    strand = hsp.strand
                    if hsp.expect< E_VALUE_THRESH and total_match > MATCH_LENGTH:
                        print("******Alignments******")
                        print("sequence:", contig_name) ## name of contig in file 
                        print("length of contig: {}".format(contig_length)) ## length of whole contig
                        print("query_match_start_residue: {}, query_match_end_residue: {}".format(query_match_start, query_match_end))
                        print("sequence match start: {}, sequence match end: {}".format(contig_match_start , contig_match_end))
                        print("e value:", e_value)
                        print("BLAST score:", BLAST_score)
                        print("strand : {}". format(strand))
                        print(hsp.query[0:100]) ## search seq
                        print(hsp.match[0:100]) ## lines connecting them
                        print(hsp.sbjct[0:100]) ## contig matched 



query CHECK1


******Alignments******
sequence: contig_2-Chymomyza-costata-Sapporo-line- No definition line
length of contig: 484
query_match_start_residue: 1, query_match_end_residue: 240
sequence match start: 484, sequence match end: 245
e value: 4.54304e-126
BLAST score: 480.0
strand : ('Plus', 'Minus')
GGTTACCCGGTACTGCATAACAATGGAACCCGAACCGTAACTGGGACAGATCGAAAAGCTGGCCTGGTTTCTCGCTGTGTGTGCCGTGTTAATCCGTTTG
||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||
GGTTACCCGGTACTGCATAACAATGGAACCCGAACCGTAACTGGGACAGATCGAAAAGCTGGCCTGGTTTCTCGCTGTGTGTGCCGTGTTAATCCGTTTG
******Alignments******
sequence: contig_1-Chymomyza-costata-Sapporo-line- No definition line
length of contig: 484
query_match_start_residue: 1, query_match_end_residue: 240
sequence match start: 1, sequence match end: 240
e value: 4.54304e-126
BLAST score: 480.0
strand : ('Plus', 'Plus')
GGTTACCCGGTACTGCATAACAATGGAACCCGAACCGTAACTGGGACAGATCGAAAAGCTGGCCTGGTTTCTCGCTGTGTGTGCCGTGTTAATCCGT

In [290]:
## make a blast search with gene and jakes minimal enhacer to the database to select only contigs with both the gene and the enhancer 
! mkdir -p database/output
cline = NcbiblastnCommandline(query="../sequences/queries/D.mel_full_query.fasta" , db="../database/all_genomes_db", strand="both", evalue=1000, out="../database/output/jake_enhancer.xml", outfmt=5, task= "dc-megablast")
cline
print(cline)
cline()

blastn -out ../database/output/jake_enhancer.xml -outfmt 5 -query ../sequences/queries/D.mel_full_query.fasta -db ../database/all_genomes_db -evalue 1000 -strand both -task dc-megablast


('', '')

In [218]:
dics = defaultdict(list)

E_VALUE_THRESH = 100
for record in NCBIXML.parse(open("../database/output/gene_and_enhancer.xml", 'r')):
    for desc in record.descriptions:
        if desc.e < E_VALUE_THRESH:
            chosen_contig = desc.title
            for alignment in record.alignments:
                for hsp in alignment.hsps:
                    contig_length= alignment.length
                    contig_title = alignment.title
                    contig_title_list = contig_title.split("-")
                    length_title = len(contig_title_list)-1
                    contig_name = contig_title_list[:length_title]
                    name = "-".join(contig_name)
                    query_match_start = hsp.query_start
                    query_match_end = hsp.query_end
                    contig_match_start = hsp.sbjct_start
                    contig_match_end = hsp.sbjct_end
                    total_match = query_match_end - query_match_start
                    e_value = hsp.expect
                    strand = hsp.strand
                    if contig_title == chosen_contig and e_value < .0001:
                        if contig_match_start-15000 >0 and contig_match_end+15000 < contig_length:
                            dics[name].append([contig_match_start-13000,contig_match_end+1300])
                        elif contig_match_start-15000 >0 and contig_match_end+15000 < contig_length:
                            dics[name].append([contig_match_start-10000,contig_match_end+1000])
                        else:
                            dics[name].append([contig_match_start-5000,contig_match_end+500])                       



TypeError: must be str or None, not int

In [72]:
dics

defaultdict(list,
            {'contig_1-Drosophila-ambigua-R42-Mt-Rtanj-': [[8231775, 8246025]],
             'contig_1-Drosophila-equinoxialis-14030-0741-00': [[1588521,
               1602754]],
             'contig_1-Drosophila-melanogaster-14021-0231-36': [[6242908,
               6257691],
              [3405314, 3419657]],
             'contig_1-Drosophila-pseudoananassae': [[6489897, 6504535]],
             'contig_1-Drosophila-sucinea-14030-0791-01': [[18938843,
               18953283]],
             'contig_107-Drosophila-takahashii-IR98-3-E-12201': [[7183134,
               7196968]],
             'contig_1070-Drosophila-persimilis-14011-0111-01': [[1893109,
               1907448]],
             'contig_113-Drosophila-jambulina-14028-0671-01': [[13027536,
               13041678],
              [13027222, 13041384],
              [17378668, 17392910],
              [14823223, 14837478]],
             'contig_1143-Drosophila-teissieri-CT02': [[3600162, 3613920]],
          

In [73]:
dic = {}
for k,v in dics.items():
    if len(v[0]) == 2:
        dic[k] = v[0]

In [75]:
with open("../sequences/test_file.fasta", 'r') as fhread:
    with open("../sequences/eve_enhancer_extracted.fasta", "w") as fhwrite:
        for rec in SeqIO.parse(fhread, 'fasta'):
            name = rec.id[:-1]
            seq = rec.seq
            seqLen = len(rec)
            if name in dic:
                start = dic[name][0]
                end = dic[name][1]
                seq_new = seq[start:end]
                fhwrite.write(">{}\n".format(name))
                fhwrite.write("{}\n".format(seq_new))

In [456]:
## retrieve dataset: 
E_VALUE_THRESH = 100

with open("../sequences/D.mel_gene_and_enhancer.txt","w") as fh:
    uniques = set()
    for record in NCBIXML.parse(open("../database/output/module_blast.xml", 'r')):
        for desc in record.descriptions:
            if desc.e < E_VALUE_THRESH:
                chosen_contig = desc.title
                for alignment in record.alignments:
                    for hsp in alignment.hsps:
                        contig_length= alignment.length
                        contig_name = alignment.title
                        query_match_start = hsp.query_start
                        query_match_end = hsp.query_end
                        contig_match_start = hsp.sbjct_start
                        contig_match_end = hsp.sbjct_end
                        total_match = query_match_end - query_match_start
                        e_value = hsp.expect
                        strand = hsp.strand
                        sequence = hsp.sbjct
                        split = contig_name.split(" ")
                        if contig_name == chosen_contig and e_value < .001:
                            uniques.add(split[0])
                        
                        #if contig_name == chosen_contig and e_value < 1:
                            #fh.write("contig_name_{strand}\n")

                            #fh.write("{sequence}\n")
with open("../sequences/D.mel_gene_and_enhancer.txt","w") as fh:
    for name in uniques:
        fh.write("{}\n".format(name))

In [457]:
! cat ../sequences/D.mel_gene_and_enhancer.txt | sort | wc -l

      95


In [ ]:
for record in NCBIXML.parse(open("../database/output/module_blast.xml", 'r')):
    for decs

In [5]:
eve_and_enhancer = defaultdict(list) 
enhancer = defaultdict(list)
jake_enhancer = defaultdict(list)
eve_or_enhancer = defaultdict(list) 

In [86]:
! blastdbcmd -db ../database/all_genomes_db -entry all -outfmt %i 

lcl|contig_1-Chymomyza-costata-Sapporo-line-
lcl|contig_2-Chymomyza-costata-Sapporo-line-
lcl|contig_3-Chymomyza-costata-Sapporo-line-
lcl|contig_4-Chymomyza-costata-Sapporo-line-
lcl|contig_5-Chymomyza-costata-Sapporo-line-
lcl|contig_6-Chymomyza-costata-Sapporo-line-
lcl|contig_7-Chymomyza-costata-Sapporo-line-
lcl|contig_8-Chymomyza-costata-Sapporo-line-
lcl|contig_9-Chymomyza-costata-Sapporo-line-
lcl|contig_10-Chymomyza-costata-Sapporo-line-
lcl|contig_11-Chymomyza-costata-Sapporo-line-
lcl|contig_12-Chymomyza-costata-Sapporo-line-
lcl|contig_13-Chymomyza-costata-Sapporo-line-
lcl|contig_14-Chymomyza-costata-Sapporo-line-
lcl|contig_15-Chymomyza-costata-Sapporo-line-
lcl|contig_16-Chymomyza-costata-Sapporo-line-
lcl|contig_17-Chymomyza-costata-Sapporo-line-
lcl|contig_18-Chymomyza-costata-Sapporo-line-
lcl|contig_19-Chymomyza-costata-Sapporo-line-
lcl|contig_20-Chymomyza-costata-Sapporo-line-
lcl|contig_21-Chymomyza-costata-Sapporo-line-
lcl|contig_22-Chymomyza-costata-Sapporo-lin

lcl|contig_314-Drosophila-arawakana-15182-2261-03-
lcl|contig_315-Drosophila-arawakana-15182-2261-03-
lcl|contig_316-Drosophila-arawakana-15182-2261-03-
lcl|contig_317-Drosophila-arawakana-15182-2261-03-
lcl|contig_318-Drosophila-arawakana-15182-2261-03-
lcl|contig_319-Drosophila-arawakana-15182-2261-03-
lcl|contig_320-Drosophila-arawakana-15182-2261-03-
lcl|contig_321-Drosophila-arawakana-15182-2261-03-
lcl|contig_322-Drosophila-arawakana-15182-2261-03-
lcl|contig_323-Drosophila-arawakana-15182-2261-03-
lcl|contig_324-Drosophila-arawakana-15182-2261-03-
lcl|contig_325-Drosophila-arawakana-15182-2261-03-
lcl|contig_326-Drosophila-arawakana-15182-2261-03-
lcl|contig_327-Drosophila-arawakana-15182-2261-03-
lcl|contig_328-Drosophila-arawakana-15182-2261-03-
lcl|contig_329-Drosophila-arawakana-15182-2261-03-
lcl|contig_330-Drosophila-arawakana-15182-2261-03-
lcl|contig_331-Drosophila-arawakana-15182-2261-03-
lcl|contig_332-Drosophila-arawakana-15182-2261-03-
lcl|contig_333-Drosophila-arawa

lcl|contig_417-Drosophila-cardini-15181-2181-03-
lcl|contig_1534-Drosophila-cardini-15181-2181-03-
lcl|contig_1928-Drosophila-cardini-15181-2181-03-
lcl|contig_526-Drosophila-cardini-15181-2181-03-
lcl|contig_944-Drosophila-cardini-15181-2181-03-
lcl|contig_1936-Drosophila-cardini-15181-2181-03-
lcl|contig_1622-Drosophila-cardini-15181-2181-03-
lcl|contig_2033-Drosophila-cardini-15181-2181-03-
lcl|contig_1677-Drosophila-cardini-15181-2181-03-
lcl|contig_1097-Drosophila-cardini-15181-2181-03-
lcl|contig_520-Drosophila-cardini-15181-2181-03-
lcl|contig_1110-Drosophila-cardini-15181-2181-03-
lcl|contig_792-Drosophila-cardini-15181-2181-03-
lcl|contig_2195-Drosophila-cardini-15181-2181-03-
lcl|contig_943-Drosophila-cardini-15181-2181-03-
lcl|contig_5-Drosophila-cardini-15181-2181-03-
lcl|contig_307-Drosophila-cardini-15181-2181-03-
lcl|contig_1801-Drosophila-cardini-15181-2181-03-
lcl|contig_817-Drosophila-cardini-15181-2181-03-
lcl|contig_319-Drosophila-cardini-15181-2181-03-
lcl|contig_1

lcl|contig_323-Drosophila-dunni-15182-2291-00-
lcl|contig_324-Drosophila-dunni-15182-2291-00-
lcl|contig_325-Drosophila-dunni-15182-2291-00-
lcl|contig_326-Drosophila-dunni-15182-2291-00-
lcl|contig_327-Drosophila-dunni-15182-2291-00-
lcl|contig_328-Drosophila-dunni-15182-2291-00-
lcl|contig_329-Drosophila-dunni-15182-2291-00-
lcl|contig_330-Drosophila-dunni-15182-2291-00-
lcl|contig_331-Drosophila-dunni-15182-2291-00-
lcl|contig_332-Drosophila-dunni-15182-2291-00-
lcl|contig_333-Drosophila-dunni-15182-2291-00-
lcl|contig_334-Drosophila-dunni-15182-2291-00-
lcl|contig_335-Drosophila-dunni-15182-2291-00-
lcl|contig_336-Drosophila-dunni-15182-2291-00-
lcl|contig_337-Drosophila-dunni-15182-2291-00-
lcl|contig_338-Drosophila-dunni-15182-2291-00-
lcl|contig_339-Drosophila-dunni-15182-2291-00-
lcl|contig_340-Drosophila-dunni-15182-2291-00-
lcl|contig_341-Drosophila-dunni-15182-2291-00-
lcl|contig_342-Drosophila-dunni-15182-2291-00-
lcl|contig_343-Drosophila-dunni-15182-2291-00-
lcl|contig_34

lcl|contig_2452-Drosophila-dunni-15182-2291-00-
lcl|contig_2453-Drosophila-dunni-15182-2291-00-
lcl|contig_2454-Drosophila-dunni-15182-2291-00-
lcl|contig_2455-Drosophila-dunni-15182-2291-00-
lcl|contig_2456-Drosophila-dunni-15182-2291-00-
lcl|contig_2457-Drosophila-dunni-15182-2291-00-
lcl|contig_2458-Drosophila-dunni-15182-2291-00-
lcl|contig_2459-Drosophila-dunni-15182-2291-00-
lcl|contig_2460-Drosophila-dunni-15182-2291-00-
lcl|contig_2461-Drosophila-dunni-15182-2291-00-
lcl|contig_2462-Drosophila-dunni-15182-2291-00-
lcl|contig_2463-Drosophila-dunni-15182-2291-00-
lcl|contig_2464-Drosophila-dunni-15182-2291-00-
lcl|contig_2465-Drosophila-dunni-15182-2291-00-
lcl|contig_2466-Drosophila-dunni-15182-2291-00-
lcl|contig_2467-Drosophila-dunni-15182-2291-00-
lcl|contig_2468-Drosophila-dunni-15182-2291-00-
lcl|contig_2469-Drosophila-dunni-15182-2291-00-
lcl|contig_2470-Drosophila-dunni-15182-2291-00-
lcl|contig_2471-Drosophila-dunni-15182-2291-00-
lcl|contig_2472-Drosophila-dunni-15182-2

...

lcl|contig_641-Zaprionus-tsacasi-isof-from-J--David-
lcl|contig_642-Zaprionus-tsacasi-isof-from-J--David-
lcl|contig_643-Zaprionus-tsacasi-isof-from-J--David-
lcl|contig_644-Zaprionus-tsacasi-isof-from-J--David-
lcl|contig_645-Zaprionus-tsacasi-isof-from-J--David-
lcl|contig_646-Zaprionus-tsacasi-isof-from-J--David-
lcl|contig_1-Zaprionus-vittiger-isof-from-J--David-
lcl|contig_2-Zaprionus-vittiger-isof-from-J--David-
lcl|contig_3-Zaprionus-vittiger-isof-from-J--David-
lcl|contig_4-Zaprionus-vittiger-isof-from-J--David-
lcl|contig_5-Zaprionus-vittiger-isof-from-J--David-
lcl|contig_6-Zaprionus-vittiger-isof-from-J--David-
lcl|contig_7-Zaprionus-vittiger-isof-from-J--David-
lcl|contig_8-Zaprionus-vittiger-isof-from-J--David-
lcl|contig_9-Zaprionus-vittiger-isof-from-J--David-
lcl|contig_10-Zaprionus-vittiger-isof-from-J--David-
lcl|contig_11-Zaprionus-vittiger-isof-from-J--David-
lcl|contig_12-Zaprionus-vittiger-isof-from-J--David-
lcl|contig_13-Zaprionus-vittiger-isof-from-J--David-
lc

lcl|contig_262-Zaprionus-vittiger-isof-from-J--David
lcl|contig_263-Zaprionus-vittiger-isof-from-J--David
lcl|contig_264-Zaprionus-vittiger-isof-from-J--David
lcl|contig_265-Zaprionus-vittiger-isof-from-J--David
lcl|contig_266-Zaprionus-vittiger-isof-from-J--David
lcl|contig_267-Zaprionus-vittiger-isof-from-J--David
lcl|contig_268-Zaprionus-vittiger-isof-from-J--David
lcl|contig_269-Zaprionus-vittiger-isof-from-J--David
lcl|contig_270-Zaprionus-vittiger-isof-from-J--David
lcl|contig_271-Zaprionus-vittiger-isof-from-J--David
lcl|contig_272-Zaprionus-vittiger-isof-from-J--David
lcl|contig_273-Zaprionus-vittiger-isof-from-J--David
lcl|contig_274-Zaprionus-vittiger-isof-from-J--David
lcl|contig_275-Zaprionus-vittiger-isof-from-J--David
lcl|contig_276-Zaprionus-vittiger-isof-from-J--David
lcl|contig_277-Zaprionus-vittiger-isof-from-J--David
lcl|contig_278-Zaprionus-vittiger-isof-from-J--David
lcl|contig_279-Zaprionus-vittiger-isof-from-J--David
lcl|contig_280-Zaprionus-vittiger-isof-from-J-

lcl|contig_509-Zaprionus-vittiger-isof-from-J--David
lcl|contig_510-Zaprionus-vittiger-isof-from-J--David
lcl|contig_511-Zaprionus-vittiger-isof-from-J--David
lcl|contig_512-Zaprionus-vittiger-isof-from-J--David
lcl|contig_513-Zaprionus-vittiger-isof-from-J--David
lcl|contig_514-Zaprionus-vittiger-isof-from-J--David
lcl|contig_515-Zaprionus-vittiger-isof-from-J--David
lcl|contig_516-Zaprionus-vittiger-isof-from-J--David
lcl|contig_517-Zaprionus-vittiger-isof-from-J--David
lcl|contig_518-Zaprionus-vittiger-isof-from-J--David
lcl|contig_519-Zaprionus-vittiger-isof-from-J--David
lcl|contig_520-Zaprionus-vittiger-isof-from-J--David
lcl|contig_522-Zaprionus-vittiger-isof-from-J--David
lcl|contig_523-Zaprionus-vittiger-isof-from-J--David
lcl|contig_524-Zaprionus-vittiger-isof-from-J--David
lcl|contig_525-Zaprionus-vittiger-isof-from-J--David
lcl|contig_526-Zaprionus-vittiger-isof-from-J--David
lcl|contig_527-Zaprionus-vittiger-isof-from-J--David
lcl|contig_528-Zaprionus-vittiger-isof-from-J-

lcl|contig_777-Zaprionus-vittiger-isof-from-J--David
lcl|contig_778-Zaprionus-vittiger-isof-from-J--David
lcl|contig_779-Zaprionus-vittiger-isof-from-J--David
lcl|contig_780-Zaprionus-vittiger-isof-from-J--David
lcl|contig_781-Zaprionus-vittiger-isof-from-J--David
lcl|contig_782-Zaprionus-vittiger-isof-from-J--David
lcl|contig_783-Zaprionus-vittiger-isof-from-J--David
lcl|contig_784-Zaprionus-vittiger-isof-from-J--David
lcl|contig_785-Zaprionus-vittiger-isof-from-J--David
lcl|contig_786-Zaprionus-vittiger-isof-from-J--David
lcl|contig_787-Zaprionus-vittiger-isof-from-J--David
lcl|contig_788-Zaprionus-vittiger-isof-from-J--David
lcl|contig_789-Zaprionus-vittiger-isof-from-J--David
lcl|contig_790-Zaprionus-vittiger-isof-from-J--David
lcl|contig_791-Zaprionus-vittiger-isof-from-J--David
lcl|contig_792-Zaprionus-vittiger-isof-from-J--David
lcl|contig_793-Zaprionus-vittiger-isof-from-J--David
lcl|contig_794-Zaprionus-vittiger-isof-from-J--David
lcl|contig_795-Zaprionus-vittiger-isof-from-J-

lcl|contig_986-Zaprionus-vittiger-isof-from-J--David
lcl|contig_987-Zaprionus-vittiger-isof-from-J--David
lcl|contig_988-Zaprionus-vittiger-isof-from-J--David
lcl|contig_989-Zaprionus-vittiger-isof-from-J--David
lcl|contig_990-Zaprionus-vittiger-isof-from-J--David
lcl|contig_991-Zaprionus-vittiger-isof-from-J--David
lcl|contig_992-Zaprionus-vittiger-isof-from-J--David
lcl|contig_993-Zaprionus-vittiger-isof-from-J--David
lcl|contig_994-Zaprionus-vittiger-isof-from-J--David
lcl|contig_995-Zaprionus-vittiger-isof-from-J--David
lcl|contig_996-Zaprionus-vittiger-isof-from-J--David
lcl|contig_997-Zaprionus-vittiger-isof-from-J--David
lcl|contig_998-Zaprionus-vittiger-isof-from-J--David
lcl|contig_999-Zaprionus-vittiger-isof-from-J--David
lcl|contig_1000-Zaprionus-vittiger-isof-from-J--Davi
lcl|contig_1001-Zaprionus-vittiger-isof-from-J--Davi
lcl|contig_1002-Zaprionus-vittiger-isof-from-J--Davi
lcl|contig_1003-Zaprionus-vittiger-isof-from-J--Davi
lcl|contig_1004-Zaprionus-vittiger-isof-from-J

In [37]:
## Quick visual evaluation
E_VALUE_THRESH = .1
MATCH_LENGTH = 100
for record in NCBIXML.parse(open("../database/output/gene_or_enhancer.xml", 'r')):
     if record.alignments:
            query = record.query[0:100].upper()
            print("\n")
            print("query", query)
            print("\n")
            for alignment in record.alignments:
                for hsp in alignment.hsps:
                    contig_length= alignment.length
                    contig_name = alignment.title
                    contig_name = contig_name.split()[0]
                    query_match_start = hsp.query_start
                    query_match_end = hsp.query_end
                    contig_match_start = hsp.sbjct_start
                    contig_match_end = hsp.sbjct_end
                    total_match = query_match_end - query_match_start
                    e_value = hsp.expect
                    BLAST_score = hsp.score
                    strand = hsp.strand
                    strand = strand[1].lower()
                    if hsp.expect< E_VALUE_THRESH and total_match > MATCH_LENGTH:
                        print("******Alignments******")
                        print("sequence:", contig_name) ## name of contig in file 
                        print("length of contig: {}".format(contig_length)) ## length of whole contig
                        print("query_match_start_residue: {}, query_match_end_residue: {}".format(query_match_start, query_match_end))
                        print("sequence match start: {}, sequence match end: {}".format(contig_match_start , contig_match_end))
                        print("e value:", e_value)
                        print("BLAST score:", BLAST_score)
                        print("strand : {}". format(strand))
                        print(hsp.query[0:100]) ## search seq
                        print(hsp.match[0:100]) ## lines connecting them
                        print(hsp.sbjct[0:100]) ## contig matched to
                        eve_or_enhancer[contig_name].append([query, contig_match_start, contig_match_end, strand])
                        



query DMEL_STRIPE2_MINIMAL_BRONSKY


******Alignments******
sequence: contig_1-Drosophila-melanogaster-14021-0231-36-
length of contig: 21632781
query_match_start_residue: 1, query_match_end_residue: 484
sequence match start: 6255908, sequence match end: 6256391
e value: 0.0
BLAST score: 968.0
strand : plus
GGTTACCCGGTACTGCATAACAATGGAACCCGAACCGTAACTGGGACAGATCGAAAAGCTGGCCTGGTTTCTCGCTGTGTGTGCCGTGTTAATCCGTTTG
||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||||
GGTTACCCGGTACTGCATAACAATGGAACCCGAACCGTAACTGGGACAGATCGAAAAGCTGGCCTGGTTTCTCGCTGTGTGTGCCGTGTTAATCCGTTTG
******Alignments******
sequence: contig_529-Drosophila-sechellia-14021-0248-01-
length of contig: 19765707
query_match_start_residue: 1, query_match_end_residue: 484
sequence match start: 15052653, sequence match end: 15052176
e value: 0.0
BLAST score: 894.0
strand : minus
GGTTACCCGGTACTGCATAACAATGGAACCCGAACCGTAACTGGGACAGATCGAAAAGCTGGCCTGGTTTCTCGCTGTGTGTGCCGTGTTAATCCGTTTG
|||||||||||

sequence: contig_164-Drosophila-ercepeae-14024-0432-00-
length of contig: 22310376
query_match_start_residue: 155, query_match_end_residue: 480
sequence match start: 141492, sequence match end: 141188
e value: 4.30319e-25
BLAST score: 137.0
strand : minus
TTTCACTTTCGAGTTAGACTTTATTGCAGCATCTTGAACAATCG--TCGCAGTTTGGTAACACGCTG--TGCCATACTTTC---------ATTTAGACGG
|| || |||||||||||| |||||||||||||||||||||||||  ||| |||||||||||||||||  |||  | ||| |         ||| ||    
TTCCAGTTTCGAGTTAGATTTTATTGCAGCATCTTGAACAATCGACTCGAAGTTTGGTAACACGCTGGTTGCTCTCCTTGCTGACTATCAATTGAGCAAA
******Alignments******
sequence: contig_131-Drosophila-varians-CKM15-L1-
length of contig: 22423966
query_match_start_residue: 138, query_match_end_residue: 480
sequence match start: 22261798, sequence match end: 22261476
e value: 1.50196e-24
BLAST score: 134.0
strand : minus
TTTCGCTTTCGTCCTCGTTTCACTTTCGAGTTAGACTTTATTGCAGCATCTTGAACAATCG--TCGCAGTTTGGTAACACGCTG--TGCCATACTTTC--
|||| ||||| | ||  || || |||||||||||| |||||||||||||||||||||||||  

strand : minus
ATGCACGGATACCGAACCTACAACATGGAGAGCCACCATGCCCATCACGACGCCAGTCCCG---TGGACCAGAAGCCCCTGGTTGTGGACCTCTTGGCCA
|||||||||||  |||||||| | |||||||  || ||||| |||||  ||| ||   |||   |||| ||||| ||  ||||||| || ||| |  || 
ATGCACGGATATAGAACCTACCAAATGGAGAATCATCATGCACATCAACACGACAACACCGCGGTGGATCAGAAACCGTTGGTTGTTGATCTCATTTCCG
******Alignments******
sequence: contig_828-Drosophila-paulistorum-L06-
length of contig: 52051736
query_match_start_residue: 1, query_match_end_residue: 247
sequence match start: 37373674, sequence match end: 37373929
e value: 2.64939e-30
BLAST score: 155.0
strand : plus
ATGCACGGATACCGAACCTACAACATGGAGAGCCACCATGCCCATCACGACGCCAGTCCCG---TGGACCAGAAGCCCCTGGTTGTGGACCTCTTGGCCA
|||||||||||  ||||||||||||||||||  || ||||| |||||  ||| ||   |||   |||| ||||| || |||||||| || ||| |  || 
ATGCACGGATATAGAACCTACAACATGGAGAATCATCATGCACATCAACACGACAACACCGCGGTGGATCAGAAACCGCTGGTTGTTGATCTCATTTCCG
******Alignments******
sequence: contig_695-Lordiphosa-collinella-50-wild-caught-
length of contig: 171193

In [81]:
len(eve_or_enhancer)

126

In [82]:
selected_contigs = defaultdict(list)

In [41]:
count = 0
for k, v in eve_or_enhancer.items():
    if v[0][0] != "DMEL_STRIPE2_GENE_NCBI":
        selected_contigs[k].append(v[0])
        count +=1
print(count)


102


In [42]:
for k,v in selected_contigs.items():
    print(k)
    print(v)

contig_1-Drosophila-melanogaster-14021-0231-36-
[['DMEL_STRIPE2_MINIMAL_BRONSKY', 6255908, 6256391, 'plus']]
contig_529-Drosophila-sechellia-14021-0248-01-
[['DMEL_STRIPE2_MINIMAL_BRONSKY', 15052653, 15052176, 'minus']]
contig_203-Drosophila-simulans-14021-0251-006-
[['DMEL_STRIPE2_MINIMAL_BRONSKY', 4606809, 4607280, 'plus']]
contig_22-Drosophila-mauritiana-14021-0241-01-
[['DMEL_STRIPE2_MINIMAL_BRONSKY', 3990590, 3991074, 'plus']]
contig_1143-Drosophila-teissieri-CT02-
[['DMEL_STRIPE2_MINIMAL_BRONSKY', 3613162, 3612620, 'minus']]
contig_704-Drosophila-teissieri-273-3-
[['DMEL_STRIPE2_MINIMAL_BRONSKY', 4411504, 4410956, 'minus']]
contig_508-Drosophila-erecta-14021-0224-01-
[['DMEL_STRIPE2_MINIMAL_BRONSKY', 13609130, 13609683, 'plus']]
contig_185-Drosophila-yakuba-14021-0261-01-
[['DMEL_STRIPE2_MINIMAL_BRONSKY', 3041935, 3041439, 'minus']]
contig_115-Drosophila-rhopaloa-14029-0021-01-
[['DMEL_STRIPE2_MINIMAL_BRONSKY', 12680605, 12681085, 'plus']]
contig_762-Drosophila-fuyamai-14029-0011

In [9]:
selected_contigs["contig_1-Drosophila-melanogaster-14021-0231-36-"]

[['DMEL_STRIPE2_MINIMAL_BRONSKY', 6255908, 6256391, 'plus']]

In [75]:
len(selected_contigs)

with open("../sequences/short_selected_contigs.txt", "w") as fh:
    for k, v in selected_contigs.items():
        if v[0][3] == "plus":
            start = int(v[0][1])
            start = start - 500
            end = int(v[0][2])
            end = end + 500
            strand = v[0][3]
            fh.write("{} {} {}-{}\n".format(k,strand,start,end))
        else:
            start = int(v[0][2])
            start = start - 500
            end = int(v[0][1])
            end = end + 500
            strand = v[0][3]
            fh.write("{} {} {}-{} \n".format(k,strand,start,end))
            

In [76]:
! cat ../sequences/short_selected_contigs.txt | awk -F'-' '{print $2,$3,$4}' | sort | uniq -d | wc -l

      23


In [77]:
! cat ../sequences/short_selected_contigs.txt | awk -F'-' '{print $2,$3,$4}' | sort | uniq -u | wc -l

      52


In [80]:
! cat ../sequences/short_selected_contigs.txt | awk -F'-' '{print $2,$3,$4}' | sort | wc -l

     102


In [148]:
count = 0
for k, v in eve_or_enhancer.items():
    if len(v) >2:
        if abs((v[1][3]-v[0][3])) > 10000:
            print(k)
            print(v[1][3]-v[0][3])
            count +=1
print(count)

contig_131-Drosophila-varians-CKM15-L1- No definition line
-14984279
contig_149-Drosophila-elegans-14027-0461-03- No definition line
1014678
2


In [283]:
len("GGTTACCCGGTACTGCATAACAATGGAACCCGAACCGTAACTGGGACAGATCGAAAAGCTGGCCTGGTTTCTCGCTGTGTGTGCCGTGTTAATCCGTTTGCCATCAGCGAGATTATTAGTCAATTGCAGTTGCAGCGTTTCGCTTTCGTCCTCGTTTCACTTTCGAGTTAGACTTTATTGCAGCATCTTGAACAATCGTCGCAGTTTGGTAACACGCTGTGCCATACTTTCATTTAGACGGAATCGAGGGACCCTGGACTATAATCGCACAACGAGACCGGGTTGCGAAGTCAGGGCATTCCGCCGATCTAGCCATCGCCATCTTCTGCGGGCGTTTGTTTGTTTGTTTGCTGGGATTAGCCAAGGGCTTGACTTGGAATccaatcccgatccctagcccgatcccaatcccaatcccaatcccTTGTCCTTTTCATTAGAAAGTCATAAAAACACATAATAATGATGTCGAAGGGATTAGGGG")

484

In [143]:
np.diff

<function numpy.lib.function_base.diff>

In [229]:
E_VALUE_THRESH = 1000
for record in NCBIXML.parse(open("../database/output/gene_or_enhancer.xml", 'r')): 
     if record.alignments: 
        print("\n")
        print("***************** query: {} *****************".format(record.query[:100]).upper())
        count = 0
        for align in record.alignments: 
            for hsp in align.hsps: 
                if hsp.expect < E_VALUE_THRESH:
                    count = count + 1
                    print("match: %s " % align.title[:100])
        print("********* {} matches to {} percent of input sequences/species ************".format(record.query[:100], round(count/73*100)).upper())
        print("\n")




***************** QUERY: DMEL_STRIPE2_MINIMAL_BRONSKY *****************
match: contig_1-Drosophila-melanogaster-14021-0231-36- No definition line 
match: contig_1-Drosophila-melanogaster-14021-0231-36- No definition line 
match: contig_1-Drosophila-melanogaster-14021-0231-36- No definition line 
match: contig_1-Drosophila-melanogaster-14021-0231-36- No definition line 
match: contig_529-Drosophila-sechellia-14021-0248-01- No definition line 
match: contig_529-Drosophila-sechellia-14021-0248-01- No definition line 
match: contig_203-Drosophila-simulans-14021-0251-006- No definition line 
match: contig_203-Drosophila-simulans-14021-0251-006- No definition line 
match: contig_203-Drosophila-simulans-14021-0251-006- No definition line 
match: contig_203-Drosophila-simulans-14021-0251-006- No definition line 
match: contig_22-Drosophila-mauritiana-14021-0241-01- No definition line 
match: contig_22-Drosophila-mauritiana-14021-0241-01- No definition line 
match: contig_22-Drosophila-maurit

match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosophila-repleta-kari30- No definition line 
match: contig_382-Drosoph

In [13]:
from collections import defaultdict 

E_VALUE_THRESH = 1

results = defaultdict(list)

for record in NCBIXML.parse(open("../database/output/D.mel_blast.xml", 'r')): 
     if record.descriptions: 
        for desc in record.descriptions:
            if desc.e < E_VALUE_THRESH:
                results[record.query].append(desc.title)

if list(results["dmel_stripe2_full_jake"]).sort() == list(results["dmel_stripe2_minimal_bronsky"]).sort():
    print("lists overlap entirely")

                    

lists overlap entirely


In [284]:
len("TCCAAATATGATAAAAGTACAAAGCATACGATAATATAATCAAATTACGCTGACAATCACGATAATGTTCTTGTAGTAGT")


80

In [287]:
80*

5600